In [ ]:
import os
import zipfile
import requests
import jsonlines
from tqdm import tqdm
from pathlib import Path
from pycocotools.coco import COCO
from pycocotools import mask as maskUtils

# Download Annotations

In [ ]:
url = 'http://images.cocodataset.org/annotations/'
file = 'annotations_trainval2017.zip'
if not Path(f'./{file}').exists():
    response = requests.get(url + file)
    with open(file, 'wb') as f:
        f.write(response.content)

    with zipfile.ZipFile(file, 'r') as zipf:
        zipf.extractall(Path())


# Read annotations

In [ ]:
coco91_to_coco80 = [
    None, 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, None,
    11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22,
    23, None, 24, 25, None, None, 26, 27, 28, 29, 30,
    31, 32, 33, 34, 35, 36, 37, 38, 39, None, 40, 41,
    42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54,
    55, 56, 57, 58, 59, None, 60, None, None, 61, None,
    62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, None,
    73, 74, 75, 76, 77, 78, 79
]

# Instance Segmentation Task

In [ ]:
train_data = COCO('annotations/instances_train2017.json')
val_data = COCO('annotations/instances_val2017.json')

In [ ]:
for split, data in zip(['train', 'validation'], [train_data, val_data]):
    with jsonlines.open(f'data/instance_{split}.jsonl', mode='w') as writer:
        for image_id, image_info in tqdm(data.imgs.items()):
            bboxes, categories, instance_rles = [], [], []
            anns = data.imgToAnns[image_id]
            height, width = image_info['height'], image_info['width']
            for ann in anns:
                bboxes.append(ann['bbox'])
                categories.append(coco91_to_coco80[ann['category_id']])
                segm = ann['segmentation']
                if isinstance(segm, list):
                    rles = maskUtils.frPyObjects(segm, height, width)
                    rle = maskUtils.merge(rles)
                    rle['counts'] = rle['counts'].decode()
                elif isinstance(segm['counts'], list):
                    rle = maskUtils.frPyObjects(segm, height, width)
                    rle['counts'] = rle['counts'].decode()
                else:
                    rle = segm
                instance_rles.append(rle)
            writer.write({
                'image': image_info['file_name'],
                'bboxes': bboxes,
                'categories': categories,
                'inst.rles': instance_rles
            })

In [ ]:
for split in ['train', 'validation']:
    file_path = f'data/instance_{split}.jsonl'
    with zipfile.ZipFile(f'data/instance_{split}.zip', 'w', zipfile.ZIP_DEFLATED) as zipf:
        zipf.write(file_path, os.path.basename(file_path))